# Exploring World Historical Battle Database
Access to this database was granted by its creator and curator, [Dr. Shuhei Kitamura of Osaka University](https://osf.io/j357k). It's important we acknowledge his generosity. 

In the interest of looking at applying data science to social studies topics, Canada's involvement in world conflict is an important part of Canadian history. This database allows us to explore battles from throughout human history, and across the world.

In [30]:
import pandas as pd
import numpy as np
import plotly.express as px
import warnings
import pycountry_convert as pc
import requests

In [31]:
# Read in the data
data = pd.read_excel('data/whbd_v11.xlsx')
data2 = pd.read_csv('data/historical_battles.csv')
data = data.merge(data2,how='left')
data = data[data['year'].notna()]
data['year'] = data['year'].map(lambda x: int(x))
data.sort_values('year',inplace=True)
data

uid   bid lr                        bname  year  year_end   
142      143    53  l             Battle of Zhuolu -2500       NaN  \
143      144    53  r             Battle of Zhuolu -2500       NaN   
19448  19449  6850  l            Battle of Banquan -2500       NaN   
19449  19450  6850  r            Battle of Banquan -2500       NaN   
21481  21482  7590  r               Battle of Uruk -2271       NaN   
...      ...   ... ..                          ...   ...       ...   
17506  17507  6213  l     Battle of Baghuz Fawqani  2019       NaN   
17505  17506  6213  l     Battle of Baghuz Fawqani  2019       NaN   
17504  17505  6213  l     Battle of Baghuz Fawqani  2019       NaN   
17510  17511  6213  r     Battle of Baghuz Fawqani  2019       NaN   
18987  18988  6693  l  Second Battle of Ras al-Ayn  2019       NaN   

                                                   war   
142                                                NaN  \
143                                                NaN   
19448                                              NaN   
19449                                              NaN   
21481                                              NaN   
...                                                ...   
17506                            Deir ez-Zor offensive   
17505                            Deir ez-Zor offensive   
17504                            Deir ez-Zor offensive   
17510                            Deir ez-Zor offensive   
18987  2019 Turkish offensive into north-eastern Syria   

                         bell  mult_sides   win  ...  entire  unknown   
142            Yanhuang tribe         NaN   win  ...     NaN      NaN  \
143              Jiuli tribes         NaN  loss  ...     NaN      NaN   
19448        Shennong (tribe)         NaN  loss  ...     NaN      NaN   
19449        Youxiong (tribe)         NaN   win  ...     NaN      NaN   
21481  Sumerian provinces (?)         NaN  loss  ...     NaN      NaN   
...                       ...         ...   ...  ...     ...      ...   
17506          United Kingdom         NaN   win  ...     NaN      NaN   
17505                  France         NaN   win  ...     NaN      NaN   
17504           United States         NaN   win  ...     NaN      NaN   
17510         Wilayat al-Sham         NaN  loss  ...     NaN      NaN   
18987                  Turkey         NaN   win  ...     NaN      NaN   

       ongoing  plan  nopage                                    wd_url   
142        NaN   NaN     NaN   http://www.wikidata.org/entity/Q1064923  \
143        NaN   NaN     NaN   http://www.wikidata.org/entity/Q1064923   
19448      NaN   NaN     NaN    http://www.wikidata.org/entity/Q755758   
19449      NaN   NaN     NaN    http://www.wikidata.org/entity/Q755758   
21481      NaN   NaN     NaN   http://www.wikidata.org/entity/Q3309009   
...        ...   ...     ...                                       ...   
17506      NaN   NaN     NaN  http://www.wikidata.org/entity/Q61843818   
17505      NaN   NaN     NaN  http://www.wikidata.org/entity/Q61843818   
17504      NaN   NaN     NaN  http://www.wikidata.org/entity/Q61843818   
17510      NaN   NaN     NaN  http://www.wikidata.org/entity/Q61843818   
18987      NaN   NaN     NaN  http://www.wikidata.org/entity/Q71414999   

                                                  wp_url  casualties   
142       https://en.wikipedia.org/wiki/Battle_of_Zhuolu         NaN  \
143       https://en.wikipedia.org/wiki/Battle_of_Zhuolu         NaN   
19448    https://en.wikipedia.org/wiki/Battle_of_Banquan         NaN   
19449    https://en.wikipedia.org/wiki/Battle_of_Banquan         NaN   
21481       https://en.wikipedia.org/wiki/Battle_of_Uruk         NaN   
...                                                  ...         ...   
17506  https://en.wikipedia.org/wiki/Battle_of_Baghuz...         NaN   
17505  https://en.wikipedia.org/wiki/Battle_of_Baghuz...         NaN   
17504  https://en.wikipedia.org/wiki/Battle_of_Baghuz... 

In [32]:
# See what the columns contain
data.columns

Index(['uid', 'bid', 'lr', 'bname', 'year', 'year_end', 'war', 'bell',
       'mult_sides', 'win', 'uk', 'fr', 'de', 'sp', 'sw', 'tr', 'at', 'ru',
       'nl', 'it', 'pt', 'dk', 'habsburg', 'hre', 'lat', 'lng', 'locn',
       'naval', 'river', 'lake', 'air', 'multiple', 'entire', 'unknown',
       'ongoing', 'plan', 'nopage', 'wd_url', 'wp_url', 'casualties',
       'True Location', 'continent'],
      dtype='object')

In [48]:
country_of_interest = 'France' #you can change this to a country you are interested in

# Filter to only look at the battles that specify Canada as a combatant. Drop unused columns
country_data = data[data['bell']==country_of_interest].drop(['uk', 'fr', 'de', 'sp', 'sw', 'tr', 'at', 
                                             'ru', 'nl', 'it', 'pt', 'dk', 'habsburg', 'hre',
                                             'naval', 'river', 'lake', 'air', 'multiple', 'entire',
                                             'ongoing', 'plan', 'nopage', 'unknown'], axis=1)
display(country_data)

uid   bid lr                       bname  year  year_end   
5248    5249  1763  r            Battle of Gisors  1198       NaN  \
1968    1969   659  r        Battle of Arnemuiden  1338       NaN   
17477  17478  6205  l      Battle of Champtoceaux  1341       NaN   
2232    2233   742  r    Battle of St Pol de Léon  1346       NaN   
2224    2225   740  r  Battle of La Roche-Derrien  1347       NaN   
...      ...   ... ..                         ...   ...       ...   
21426  21427  7567  l      Battle of Tabqa (2017)  2017       NaN   
9091    9092  3179  l      Battle of Raqqa (2017)  2017       NaN   
16613  16614  5893  l       Battle of In-Delimane  2018       NaN   
15993  15994  5684  l       Battle of Al Hudaydah  2018       NaN   
17505  17506  6213  l    Battle of Baghuz Fawqani  2019       NaN   

                                          war    bell  mult_sides   
5248                                      NaN  France         NaN  \
1968                       Hundred Years' War  France         NaN   
17477            War of the Breton Succession  France         NaN   
2232             War of the Breton Succession  France         NaN   
2224             War of the Breton Succession  France         NaN   
...                                       ...     ...         ...   
21426  Raqqa campaign (2016â_x0080__x0093_17)  France         NaN   
9091                 Raqqa campaign (2016–17)  France         NaN   
16613                  Northern Mali conflict  France         NaN   
15993       Al Hudaydah governorate offensive  France         NaN   
17505                   Deir ez-Zor offensive  France         NaN   

                       win        lat        lng   
5248                  loss  49.261667   1.743611  \
1968                   win  51.645000   3.373000   
17477                  win  47.315972  -1.292889   
2232                  loss  48.684959  -3.986864   
2224                  loss  48.744522  -3.256612   
...                    ...        ...        ...   
21426            major win  35.836666  38.548054   
9091                   win  35.950000  39.016667   
16613        win (partial)  16.600000   1.600000   
15993  ceasefire agreement  14.802222  42.951111   
17505                  win  34.460278  40.953611   

                                                    locn   
5248        Courcelles-lès-Gisors, Oise, Picardy, France  \
1968                       Arnemuiden (Walcheren island)   
17477                             Champtoceaux, Brittany   
2232                Saint-Pol-de-Léon, Finistère, France   
2224                            La Roche-Derrien, France   
...                                                  ...   
21426                                                NaN   
9091                     Raqqa, Raqqa Governorate, Syria   
16613                      In-Delimane, Gao Region, Mali   
15993                                 Al Hudaydah, Yemen   
17505  Al-Baghuz Fawqani and surroundings, Abu Kamal ...   

                                         wd_url   
5248    http://www.wikidata.org/entity/Q2236918  \
1968    http://www.wikidata.org/entity/Q1523324   
17477    http://www.wikidata.org/entity/Q616448   
2232    http://www.wikidata.org/entity/Q1576140   
2224    http://www.wikidata.org/entity/Q1575537   
...                                         ...   
21426  http://www.wikidata.org/entity/Q29258911   
9091   http://www.wikidata.org/entity/Q30140821   
16613  http://www.wikidata.org/entity/Q54866576   
15993  http://www.wikidata.org/entity/Q48735086   
17505  http://www.wikidata.org/entity/Q61843818   

                                                  wp_url  casualties   
5248      https://en.wikipedia.org/wiki/Battle_of_Gisors         NaN  \
1968   https://en.wikipedia.org/wiki/Battle_of_Arnemu...         NaN   
17477  https://en.wikipedia.org/wiki/Battle_of_Champt...         NaN   
2232   https://en.wikipedia.org/wiki/Battle_of_St_Pol...         NaN   
2224   https://en.wikipedia.org/

We can take the data and consider only the wars that list Canada as a participant:

In [49]:
country_data = country_data[country_data['bname'].notna()]

list(country_data['bname'].sort_values().unique())

['3rd battle of Gao',
 '4th battle of Gao',
 '5th Battle of Gao',
 'Action at Cherbourg',
 'Action of 10 April 1795',
 'Action of 13 January 1797',
 'Action of 13 March 1806',
 'Action of 18 June 1799',
 'Action of 27 June 1798',
 'Action of 30 May 1798',
 'Action of 6 July 1746',
 'Action of 8 June 1755',
 'Action of March 1677',
 'Action of the Hohenzollern Redoubt',
 'Armada of 1779',
 'Attack on Mers-el-Kébir',
 'Battle at Port-la-Joye',
 'Battle at The Lizard',
 'Battle of Abbeville',
 'Battle of Abukir (1799)',
 'Battle of Abukir (1801)',
 'Battle of Adwa',
 'Battle of Ajdabiya',
 'Battle of Al Hudaydah',
 'Battle of Al jurf',
 'Battle of Alasay',
 'Battle of Albert',
 'Battle of Albuera',
 'Battle of Alcantara',
 'Battle of Alexandria',
 'Battle of Algiers',
 'Battle of Alkmaar',
 'Battle of Almonacid',
 'Battle of Altenheim',
 'Battle of Amiens',
 'Battle of Amstetten',
 'Battle of Arara',
 'Battle of Arnemuiden',
 'Battle of Arras',
 'Battle of Arroyo dos Molinos',
 'Battle of

We can plot the battles on a map with their lattitude and longitude coordinates.

You can drag to move around the map, zoom in and out to get more clarity. Hovering over each data point lists the name of the battle, as well as the war in which the battle was fought.

In [50]:
fig = px.scatter_geo(country_data, lat='lat', lon='lng', 
               hover_name='bname', 
               hover_data=['year'],
               color= 'war',
               title='Battles participated in by post-Confederation Canada')

fig.update_layout(showlegend=False)
fig.show()

Let's animate through the years so see the wars that Canada has participated in

In [51]:
warnings.filterwarnings("ignore")
years = list(country_data['year'].unique())

animate_country_data = pd.DataFrame(country_data)

def animation_years(row):
    global animate_country_data
   
    df = pd.DataFrame(columns=animate_country_data.columns)
    index = years.index(row['year'])
    for i in years[index+1:]:
        row[4] = i
        df.loc[len(df.index)] = row
    
    animate_country_data = pd.concat([animate_country_data,df],ignore_index=True)

for i in range(len(country_data.index)):
    animation_years(country_data.iloc[i])



In [52]:
def rank_rows(df):
    
    df['sort_rank'] = 0
    curr_rank = 1
    for b in battles:
        temp = df.loc[df['bname'] == b]
        for i,rows in temp.iterrows():
            
            if df['sort_rank'][i] == 0:
                df['sort_rank'][i] = curr_rank
                curr_rank += 1
    return df        
            

    
animate_country_data.sort_values(['year'],inplace=True)            
battles = list(animate_country_data.sort_values('year')['bname'].unique())
animate_country_data = rank_rows(animate_country_data)

animate_country_data.sort_values('sort_rank',inplace=True)
animate_country_data

uid   bid lr                     bname  year year_end   
0       5249  1763  r          Battle of Gisors  1198      NaN  \
619     5249  1763  r          Battle of Gisors  1338      NaN   
620     5249  1763  r          Battle of Gisors  1341      NaN   
621     5249  1763  r          Battle of Gisors  1346      NaN   
622     5249  1763  r          Battle of Gisors  1347      NaN   
...      ...   ... ..                       ...   ...      ...   
617    15994  5684  l     Battle of Al Hudaydah  2018      NaN   
47415  15994  5684  l     Battle of Al Hudaydah  2019      NaN   
616    16614  5893  l     Battle of In-Delimane  2018      NaN   
47414  16614  5893  l     Battle of In-Delimane  2019      NaN   
618    17506  6213  l  Battle of Baghuz Fawqani  2019      NaN   

                                     war    bell mult_sides   
0                                    NaN  France        NaN  \
619                                  NaN  France        NaN   
620                                  NaN  France        NaN   
621                                  NaN  France        NaN   
622                                  NaN  France        NaN   
...                                  ...     ...        ...   
617    Al Hudaydah governorate offensive  France        NaN   
47415  Al Hudaydah governorate offensive  France        NaN   
616               Northern Mali conflict  France        NaN   
47414             Northern Mali conflict  France        NaN   
618                Deir ez-Zor offensive  France        NaN   

                       win        lat        lng   
0                     loss  49.261667   1.743611  \
619                   loss  49.261667   1.743611   
620                   loss  49.261667   1.743611   
621                   loss  49.261667   1.743611   
622                   loss  49.261667   1.743611   
...                    ...        ...        ...   
617    ceasefire agreement  14.802222  42.951111   
47415  ceasefire agreement  14.802222  42.951111   
616          win (partial)       16.6        1.6   
47414        win (partial)       16.6        1.6   
618                    win  34.460278  40.953611   

                                                    locn   
0           Courcelles-lès-Gisors, Oise, Picardy, France  \
619         Courcelles-lès-Gisors, Oise, Picardy, France   
620         Courcelles-lès-Gisors, Oise, Picardy, France   
621         Courcelles-lès-Gisors, Oise, Picardy, France   
622         Courcelles-lès-Gisors, Oise, Picardy, France   
...                                                  ...   
617                                   Al Hudaydah, Yemen   
47415                                 Al Hudaydah, Yemen   
616                        In-Delimane, Gao Region, Mali   
47414                      In-Delimane, Gao Region, Mali   
618    Al-Baghuz Fawqani and surroundings, Abu Kamal ...   

                                         wd_url   
0       http://www.wikidata.org/entity/Q2236918  \
619     http://www.wikidata.org/entity/Q2236918   
620     http://www.wikidata.org/entity/Q2236918   
621     http://www.wikidata.org/entity/Q2236918   
622     http://www.wikidata.org/entity/Q2236918   
...                                         ...   
617    http://www.wikidata.org/entity/Q48735086   
47415  http://www.wikidata.org/entity/Q48735086   
616    http://www.wikidata.org/entity/Q54866576   
47414  http://www.wikidata.org/entity/Q54866576   
618    http://www.wikidata.org/entity/Q61843818   

                                                  wp_url casualties   
0         https://en.wikipedia.org/wiki/Battle_of_Gisors        NaN  \
619       https://en.wikipedia.org/wiki/Battle_of_Gisors        NaN   
620       https://en.wikipedia.org/wiki/Battle_of_Gisors        NaN   
621       https://en.wikipedia.org/wiki/Battle_of_Gisors        NaN   
622       https://en.wikipedia.org/wiki/Battle_of_Gisors        NaN   
...                                                  ...        ...   
617

By clicking on the "play" button on the bottom we'll be able to look at the wars that Canada has found throughout the years

In [53]:
px.scatter_geo(animate_country_data, lat='lat', lon='lng', 
               height=800, hover_name='bname', 
               animation_frame= 'year',
               animation_group='war',
               title='Battles participated in by post-Confederation Canada')

Now let's add in the number of casualties of each battle that Canada has fought in. We will change the size of each bubble to match the number of casualties each battle had. Larger bubbles will indicate battles with more casualties.

In [55]:
casualties_con = country_data[country_data['casualties'].notna()]

px.scatter_geo(casualties_con, lat='lat', lon='lng', 
               height=800, hover_name='bname', 
               hover_data=['war', 'year'],
               size = 'casualties',
               color='casualties',
               title='Casualties of battles participated in by ' + country_of_interest)

We can also create a bar graph that shows the bloodiest wars that Canada has been a part of.

In [56]:
con_bloodiest_war = country_data.groupby('war',as_index=False)['casualties'].sum()
con_bloodiest_war = con_bloodiest_war[con_bloodiest_war['casualties'] > 0]
con_bloodiest_war.sort_values('casualties',inplace=True)

In [57]:
top_10_bloddiest_con_wars = con_bloodiest_war[:10:-1]

fig = px.bar(top_10_bloddiest_con_wars,x='war',y='casualties',title= country_of_interest + "'s Bloodiest Wars")

fig.show()

We can also look at which continents Canada has fought the most in.

In [72]:
countries = ['Canada','Russia','India'] #you can change and add/remove countries in this list

battles_continent = data
battles_continent = battles_continent[battles_continent['continent'].notna()]
battles_continent['interest'] = data['bell'].map(lambda x: True if x in countries else False)
battles_continent = battles_continent[battles_continent['interest'] == True]
battles_continent.rename(columns={'bell':'Country'},inplace=True)
battles_continent

uid   bid lr                                      bname  year   
1978    1979   662  r                          Battle of Poltava  1709  \
5875    5876  1978  l                            Siege of Danzig  1734   
18503  18504  6552  r                 Battle of Gross-Jägersdorf  1757   
18033  18034  6392  r                         Battle of Zorndorf  1758   
3145    3146  1055  r                       Battle of Kunersdorf  1759   
...      ...   ... ..                                        ...   ...   
5584    5585  1881  l                    2016 Khanasir offensive  2016   
7358    7359  2522  l  Aleppo offensive (November–December 2016)  2016   
7410    7411  2535  r         Palmyra offensive in December 2016  2016   
5167    5168  1731  r                  War in Donbass (Avdiivka)  2017   
10034  10035  3502  l                       Battle of Al-Sukhnah  2017   

       year_end                           war Country  mult_sides   
1978        NaN            Great Northern War  Russia         NaN  \
5875        NaN  War of the Polish Succession  Russia         NaN   
18503       NaN              Seven Years' War  Russia         NaN   
18033       NaN              Seven Years' War  Russia         NaN   
3145        NaN              Seven Years' War  Russia         NaN   
...         ...                           ...     ...         ...   
5584        NaN              Syrian Civil War  Russia         NaN   
7358        NaN              Battle of Aleppo  Russia         NaN   
7410        NaN              Syrian Civil War  Russia         NaN   
5167        NaN                War in Donbass  Russia         NaN   
10034       NaN                           NaN  Russia         NaN   

                                   win  ...  unknown  ongoing  plan  nopage   
1978                               win  ...      NaN      NaN   NaN     NaN  \
5875                               win  ...      NaN      NaN   NaN     NaN   
18503  win (tactical) loss (strategic)  ...      NaN      NaN   NaN     NaN   
18033                     inconclusive  ...      NaN      NaN   NaN     NaN   
3145                               win  ...      NaN      NaN   NaN     NaN   
...                                ...  ...      ...      ...   ...     ...   
5584                               win  ...      NaN      NaN   NaN     NaN   
7358                               win  ...      NaN      NaN   NaN     NaN   
7410                    loss (partial)  ...      NaN      NaN   NaN     NaN   
5167                         ceasefire  ...      NaN      NaN   NaN     NaN   
10034                              win  ...      NaN      NaN   NaN     NaN   

                                         wd_url   
1978     http://www.wikidata.org/entity/Q152486  \
5875    http://www.wikidata.org/entity/Q2354105   
18503    http://www.wikidata.org/entity/Q696689   
18033    http://www.wikidata.org/entity/Q663405   
3145     http://www.wikidata.org/entity/Q170400   
...                                         ...   
5584   http://www.wikidata.org/entity/Q22947394   
7358   http://www.wikidata.org/entity/Q27894014   
7410   http://www.wikidata.org/entity/Q27988133   
5167   http://www.wikidata.org/entity/Q22117640   
10034  http://www.wikidata.org/entity/Q35152308   

                                                  wp_url  casualties   
1978     https://en.wikipedia.org/wiki/Battle_of_Poltava         NaN  \
5875   https://en.wikipedia.org/wiki/Siege_of_Danzig_...         NaN   
18503  https://en.wikipedia.org/wiki/Battle_of_Gross-...         NaN   
18033   https://en.wikipedia.org/wiki/Battle_of_Zorndorf         NaN   
3145   https://en.wikipedia.org/wiki/Battle_of_Kuners...         NaN   
...                                                  ...         ...   
5584   https://en.wikipedia.org/wiki/2016_Khanasir_of...         NaN   
7358   https://en.wikipedia.org/wiki/Aleppo_offensive...         NaN   
7410   https://en.wikipedia.org/wiki/Palmyra_offensiv...         NaN   
5167    h

In [69]:
continent_grouped = battles_continent.groupby(['continent','bell'])['locn'].count().reset_index(name='Number of Battles Fought')
continent_grouped.sort_values('Number of Battles Fought',ascending=False,inplace=True)
fig = px.bar(continent_grouped,x='continent',y='Number of Battles Fought',color='bell',title='Number of Battles fought by each country in different Continents')
fig.show()

But these only consider battles that happened after Confederation, as the sovereign state of Canada didn't exist yet. We can also look at battles that happened in geographic Canada by only considering lattitude and longitude values in that region:

In [73]:
# Southernmost point of Canada is Lake Erie, ON, at 41°40' N; easternmost is Cape Spear, NL, at 52°37' W
# We also need to exclude a single WWII Pacific battle that happened off the coast of Alaska that didn't involve Canada
NA_data = data[(data['lat']>41.6) & 
               (data['lng']<-52.6) & 
               (data['lng']>-160)]

# There's also many wars in this subset that don't feature Canada, so we can list them here to remove:
remove = ['American Revolutionary War',
          'Sioux Wars',
          "Red Cloud's War",
          'Dakota War of 1862',
          'Russo-Tlingit War',
          'Great Sioux War of 1876',
          'Powder River Expedition',
          'American Civil War',
          'Yellowstone Expedition of 1873',
          'Nez Perce War',
          'Comanche Campaign',
          'Boston campaign',
          'Modoc War',
          'American Revolution',
          "King Philip's War",
          'Black Hawk War',
          'Colorado War',
          'American Indian Wars',
          'Forage War',
          "Coeur d'Alene War",
          'Yakima War',
          'Philadelphia campaign',
          'Ghost Dance War']

# Remove wars listed above, as well as battles without a specific war (that all happened in the USA)
NA_data = NA_data[(~NA_data['war'].isin(remove)) & (~NA_data['war'].isnull())]
          
          
          
fig = px.scatter_geo(NA_data, lat='lat', lon='lng', 
               hover_name='bname', 
               color='war',
               hover_data=['year'], 
               fitbounds='locations',
               title='Historical battles fought in present-day Canada')

fig.update_layout(showlegend=False)
fig.show()

In [45]:
list(NA_data['bname'].sort_values().unique())

['Action of 8 June 1755',
 'Battle at Port-la-Joye',
 'Battle at St. Croix',
 "Battle of Baker's Farm",
 'Battle of Batoche',
 'Battle of Beauharnois',
 'Battle of Beauport',
 'Battle of Beaver Dams',
 'Battle of Big Sandy Creek',
 'Battle of Bloody Creek',
 'Battle of Brownstown',
 'Battle of Buffalo',
 'Battle of Carillon',
 'Battle of Chedabucto',
 'Battle of Chippawa',
 "Battle of Cook's Mills",
 "Battle of Crysler's Farm",
 'Battle of Cut Knife',
 "Battle of Devil's Hole",
 'Battle of Duck Lake',
 'Battle of Eccles Hill',
 'Battle of Fish Creek',
 'Battle of Fort Albany',
 'Battle of Fort Beauséjour',
 'Battle of Fort Bull',
 'Battle of Fort Dearborn',
 'Battle of Fort Erie',
 'Battle of Fort Frontenac',
 'Battle of Fort George',
 'Battle of Fort Loyal',
 'Battle of Fort Niagara',
 'Battle of Fort Oswego',
 'Battle of Fort Pitt',
 "Battle of Frenchman's Butte",
 "Battle of Frenchman's Creek",
 'Battle of Frenchtown',
 'Battle of Fundy Bay',
 'Battle of Grand Pré',
 'Battle of Hamp

Similar to before, we can also include casualties into this and have the bubble sizes match the number of casualties

In [46]:
NA_casualties = NA_data[NA_data['casualties'].notna()]

px.scatter_geo(NA_casualties, lat='lat', lon='lng', 
               height=800, hover_name='bname', 
               size = 'casualties',
               size_max = 30,
               color = 'casualties',
               hover_data=['war','year'], 
               fitbounds='locations',
               title='Historical battles fought in present-day Canada')

In [74]:
fig = px.scatter_mapbox(NA_data, lat="lat", lon="lng", hover_name="bname", hover_data=['year'],
                        color_discrete_sequence=["fuchsia"],zoom=2.5)
fig.update_layout(
    mapbox_style="white-bg",
    mapbox_layers=[
        {
            "below": 'traces',
            "sourcetype": "raster",
            "sourceattribution": "United States Geological Survey",
            "source": [
                "https://basemap.nationalmap.gov/arcgis/rest/services/USGSImageryOnly/MapServer/tile/{z}/{y}/{x}"
            ]
        }
      ])
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

## Next Steps

Though the data can be kind of spotty for some battles, it could be interesting to bring in the number (or rate) of casualities for each battle, and size the markers proportional to that. It's only an estimate of the importance of the battle, but it's a good first step.

We could also use the plotting function to animate the conflicts throughout Canadian history.

Lastly, we could focus on WWI or WWII data and look at the advance of the Allied gains in Europe, highlighting battles that Canada was a major part of.